In [20]:
# OPERATING SYSTEM STUFF
import os
import io
import gc

# DATA SCIENCE
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

# API STUFF
import xlrd
import requests
import json

# SQL
from sqlalchemy import create_engine, text
from sqlalchemy.exc import ProgrammingError # ProgrammingError catches SQL write exceptions
from sqlalchemy import String, Integer, Float, Boolean
from sqlalchemy import create_engine, MetaData, Table, select
from sqlalchemy.sql import and_
from sqlalchemy import create_engine, MetaData, Table, select

# GEOCODING
from geopy.geocoders import GoogleV3

# CONFIGURATION FILES
import config
pd.set_option('display.float_format', '{:.6f}'.format)

# OTHER
from tqdm.notebook import tqdm

In [82]:
# FUNCTION DECLARATIONS

def geolocate(row):
    if not row['GEOCODING ERR']:  # If GEOCODING ERR is False, run the geocoding API
        address = ', '.join([row['ADDRESS'],
                             #row['NEIGHBORHOOD'],
                             row['BOROUGH']]) + ', New York City'
        response = requests.get(f'https://maps.googleapis.com/maps/api/geocode/json?address={address}&key={config.GOOGLE_API_KEY}')
        res = response.json()
        if res['results']:
            location = res['results'][0]
            if location.get('partial_match'):  # Check for partial match
                row['GEOCODING ERR'] = True
                row['LATITUDE'] = None
                row['LONGITUDE'] = None
            else:
                row['LATITUDE'] = location['geometry']['location']['lat']
                row['LONGITUDE'] = location['geometry']['location']['lng']
        else:
            row['GEOCODING ERR'] = True  # Update GEOCODING ERR to True if geolocation failed
            row['LATITUDE'] = None
            row['LONGITUDE'] = None
    return row

def print_sql_table(engine, table_name):
    """
    This function retrieves and prints all the rows from a SQL table.

    Parameters:
    engine (sqlalchemy.engine.Engine): SQLAlchemy engine instance.
    table_name (str): Name of the table in the SQL database to be printed.

    Returns:
    None. The function prints the rows of the SQL table.
    """
    metadata = MetaData()

    # Reflect the table
    table = Table(table_name, metadata, autoload_with=engine)

    # Connect to the engine
    with engine.connect() as connection:
        # Select all rows from the table
        stmt = select([table])
        result = connection.execute(stmt)

        # Print the rows
        for row in result:
            print(row)

# def upload_geocoding_dataframe_to_sql(engine, table_name, df):
#     """
#     This function uploads a pandas DataFrame to a SQL table, either appending new rows or updating existing ones.
#     The DataFrame must contain the following columns: 'BOROUGH CODE', 'BOROUGH', 'ADDRESS', 'LATITUDE', 'LONGITUDE', 'GEOCODING ERR'.
    
#     A new column 'PRIMARY_KEY' is created by concatenating 'BOROUGH CODE', 'BOROUGH', and 'ADDRESS'. This column acts as a unique identifier for each row.

#     Initially, the function tries to append all the rows from the DataFrame to the SQL table. If any duplicate 'PRIMARY_KEY' values are found, 
#     the function catches the exception and proceeds to the update operation.

#     In the update operation, for each row in the DataFrame, an UPDATE statement is executed to update the row in the SQL table with the same 'PRIMARY_KEY'. 
#     This is done by binding the column values from the DataFrame row to the parameters in the UPDATE statement.

#     Parameters:
#     engine (sqlalchemy.engine.Engine): SQLAlchemy engine instance.
#     table_name (str): Name of the table in the SQL database to which the DataFrame will be uploaded.
#     df (pandas.DataFrame): DataFrame to be uploaded. Must contain the required columns.

#     Returns:
#     None. The function operates in-place on the SQL table.
#     """
#     print("HELLOO WORLD")
#     df = df.where(pd.notnull(df), None)

#     df['PRIMARY_KEY'] = df['BOROUGH CODE'].astype(str) + '_' + df['BOROUGH'] + '_' + df['ADDRESS']

#     try:
#         print("HELLOO WORLD2")
#         df.to_sql(table_name, con=engine, index=False, if_exists='append')
#     except Exception as e:
#         print("HELLOO WORLD3")
#         print("Insert operation failed. This may be due to duplicate keys. Now attempting update operation...")
    
#     with engine.connect() as connection:
#         for i, row in df.iterrows():
#             print("HELLOO WORLD4")
#             # Update SQL statement with appropriate DataFrame column names
#             stmt = text(
#                         f"""
#                         UPDATE {table_name}
#                         SET
#                         `BOROUGH CODE` = :borough_code,
#                         BOROUGH = :borough,
#                         ADDRESS = :address,
#                         LATITUDE = :latitude,
#                         LONGITUDE = :longitude,
#                         `GEOCODING ERR` = :geocoding_err
#                         WHERE `PRIMARY_KEY` = :primary_key
#                         """
#                     )
#             print("HELLOO WORLD4.5")
#             # Replace spaces in column names with underscores and make them lowercase
#             parameters = {k.lower().replace(' ', '_'): v for k, v in row.to_dict().items()}
#             print("HELLOO WORLD4.6")
#             connection.execute(stmt, parameters)
#             print("HELLOO WORL5")

In [87]:
# FUN SQL SQLALCHEMY CODE

# Show databases
# with engine.connect() as connection:
#     result = connection.execute(text("SHOW DATABASES;"))
#     databases = [row[0] for row in result]
#     print(databases)

# Show tables
# with engine.connect() as connection:
#     result = connection.execute(text("SHOW TABLES;"))
#     tables = [row[0] for row in result]
#     print(tables)

# Show columns from table
# with engine.connect() as connection:
#     result = connection.execute(text("SHOW COLUMNS FROM geocodes;"))
#     tables = [(row[0],row[1]) for row in result]
#     print(tables)

# Show all the building classes
# This won't work unless the DataFrame 'combined' has been set up
# sorted_building_classes = sorted(
#     combined["BUILDING CLASS CATEGORY"].unique(),
#     key=lambda x: int(x.split(" ")[0])
# )

In [88]:
os.environ['SQLALCHEMY_WARN_20'] = '0'
os.environ['SQLALCHEMY_SILENCE_UBER_WARNING'] = '1'

# Database params & credentials
username = 'root'
password = 'rootpassword'
hostname = 'db'
database_name = 'database_1'

# Create database connection
engine = create_engine(f'mysql+pymysql://{username}:{password}@{hostname}')

try:
    with engine.connect() as connection:
        connection.execute(text(f'CREATE DATABASE {database_name};'))
except ProgrammingError:
    pass

engine = create_engine(f'mysql+pymysql://{username}:{password}@{hostname}/{database_name}')

In [23]:
# MAP BETWEEN NYC AND ZILLOW CATEGORIES

# Define the mappings
mapping = {
    "Single-family home": ['01 ONE FAMILY DWELLINGS'],
    "Multi-family home": [
        '03 THREE FAMILY DWELLINGS',
        '07 RENTALS - WALKUP APARTMENTS',
        '08 RENTALS - ELEVATOR APARTMENTS',
        '14 RENTALS - 4-10 UNIT'
    ],
    "Apartment": [
        '07 RENTALS - WALKUP APARTMENTS',
        '08 RENTALS - ELEVATOR APARTMENTS',
        '09 COOPS - WALKUP APARTMENTS',
        '10 COOPS - ELEVATOR APARTMENTS'
    ],
    "Condo": [
        '04 TAX CLASS 1 CONDOS',
        '12 CONDOS - WALKUP APARTMENTS',
        '13 CONDOS - ELEVATOR APARTMENTS',
        '15 CONDOS - 2-10 UNIT RESIDENTIAL',
        '16 CONDOS - 2-10 UNIT WITH COMMERCIAL UNIT'
    ],
    "Co-op": [
        '09 COOPS - WALKUP APARTMENTS',
        '10 COOPS - ELEVATOR APARTMENTS',
        '17 CONDO COOPS'
    ],
    "Duplex": ['02 TWO FAMILY DWELLINGS'],
    "Townhouse": [
        '01 ONE FAMILY DWELLINGS',
        '02 TWO FAMILY DWELLINGS'
    ],
    "Brownstone": [
        '01 ONE FAMILY DWELLINGS',
        '02 TWO FAMILY DWELLINGS'
    ],
    "Row house": [
        '01 ONE FAMILY DWELLINGS',
        '02 TWO FAMILY DWELLINGS'
    ],
}

# Flatten the mapping dictionary to create a dataframe
mapping_list = [(k, v) for k, vals in mapping.items() for v in vals]
mapping_df = pd.DataFrame(
    mapping_list,
    columns=['ZILLOW CATEGORY', 'BUILDING CLASS CATEGORY']
)

# Put the map into a SQL table. Why? Not sure. Might need it later!
mapping_df.to_sql('cat_map', con=engine, index=False, if_exists='replace')

In [25]:
# URL order: [Manhattan, Bronx, Brooklyn, Queens, Staten Island]

dataURLs = [
    'https://www.nyc.gov/assets/finance/downloads/pdf/rolling_sales/'
    'rollingsales_manhattan.xlsx',
    'https://www.nyc.gov/assets/finance/downloads/pdf/rolling_sales/'
    'rollingsales_bronx.xlsx',
    'https://www.nyc.gov/assets/finance/downloads/pdf/rolling_sales/'
    'rollingsales_brooklyn.xlsx',
    'https://www.nyc.gov/assets/finance/downloads/pdf/rolling_sales/'
    'rollingsales_queens.xlsx',
    'https://www.nyc.gov/assets/finance/downloads/pdf/rolling_sales/'
    'rollingsales_statenisland.xlsx'
]
# Create an empty array that will hold our NYC Housing DataFrames
data = []

# Pull data from the NYC website
for url in dataURLs:
    # Read Excel file and skip the first 4 rows
    df = pd.read_excel(url, skiprows=4, engine="openpyxl")
    data.append(df)

In [26]:
# Combine the dataframes from the nyc housing website
combined = pd.concat(data, ignore_index=True)

# Rename the 'BOROUGH' column to 'BOROUGH CODE'
combined = combined.rename(columns={'BOROUGH': 'BOROUGH CODE'})

# Define the mapping for borough codes to borough names
borough_mapping = {1: 'MANHATTAN', 2: 'BRONX', 3: 'BROOKLYN', 4: 'QUEENS', 5: 'STATEN ISLAND'}

# Create a new 'BOROUGH' column based on 'BOROUGH CODE'
borough = combined['BOROUGH CODE'].map(borough_mapping)

# Insert the new 'BOROUGH' column into the DataFrame right after the 'BOROUGH CODE' column
combined.insert(loc=1, column='BOROUGH', value=borough)

# Remove rows that contain the string 'N/A'
combined = combined[~combined['ADDRESS'].str.contains('N/A')]

In [27]:
# Write the contents of `combined` to the `sales` SQL table...
combined.to_sql('sales', con=engine, index=False, if_exists='replace')

In [89]:
# CREATE GEOCODING TABLE & COPY TO SQL TABLE

# Table name in the SQL database
geocodes_sql_table = 'geocodes'

# Outline the columns of the DataFrame
# that will hold our new geocode information
data_types_df = {
    'BOROUGH CODE': int,
    'BOROUGH': str,
    'NEIGHBORHOOD': str,
    'ADDRESS': str,
    'LATITUDE': float,
    'LONGITUDE': float,
    'GEOCODING ERR': bool  # New column
}

'''
We will make a table in our database from
a DataFrame using SQLAlchemy...
'''

# ...
data_types_sqlalchemy = {
    'BOROUGH CODE': Integer,
    'BOROUGH': String(25),
    'NEIGHBORHOOD': String(100),
    'ADDRESS': String(255),
    'LATITUDE': Float,
    'LONGITUDE': Float,
    'GEOCODING ERR': Boolean
}

# Template Pandas DataFrame that we use to build the SQL database
# using the 'data_types_df' data structure we defined above
geocodes = pd.DataFrame(columns=data_types_df)

# Open a database connection
with engine.connect() as connection:
    try:
        # Create the table from our 'geocodes' DataFrame
        geocodes.to_sql(geocodes_sql_table, engine, # if_exists='replace',
            index=False, dtype=data_types_sqlalchemy)
        
        # Add a primary key column that corresponds to address fields
        connection.execute(text("ALTER TABLE geocodes ADD PRIMARY_KEY VARCHAR(255)"))
        print(f"Table '{geocodes_sql_table}' created in database '{database_name}'.")
    
    except ValueError:
        print(f"Table '{geocodes_sql_table}' already exists in database '{database_name}'.")
    
    except OperationalError:
        print(f"Table '{geocodes_sql_table}' in '{database_name}' already has a PRIMARY_KEY.")
    
    # Set value of primary key to concatenation of address fields
    connection.execute(
        text(
            "UPDATE geocodes SET PRIMARY_KEY = CONCAT(`BOROUGH CODE`, '_', `BOROUGH`, '_', `ADDRESS`)"
        )
    )
    
    

Table 'geocodes' already exists in database 'database_1'.


In [29]:
# Create a table of geographic information from `combined`
geocodingTable = combined[['BOROUGH CODE', 'BOROUGH', 'NEIGHBORHOOD', 'ADDRESS']].copy()
geocodingTable['LATITUDE'] = None
geocodingTable['LONGITUDE'] = None
geocodingTable['GEOCODING ERR'] = False

In [30]:
# Query the SQL database for the geocodes table
query = f"SELECT * FROM {geocodes_sql_table}"

# Execute the query and load the result into a DataFrame
df_queryResponse = pd.read_sql_query(query, engine)
#df_queryResponse = geocodingTable[:-5].copy() # Fictional, remove in prod

In [31]:
# Find any rows we downloaded from NYC that aren't already in the database
# with a mask
mask = geocodingTable[['BOROUGH CODE', 'BOROUGH', 'NEIGHBORHOOD', 'ADDRESS']].isin(
    df_queryResponse[['BOROUGH CODE', 'BOROUGH', 'NEIGHBORHOOD', 'ADDRESS']]
)
matching_rows = mask.all(axis=1)
missing_rows = geocodingTable[~matching_rows]

# Create a new row with a fictional address
new_row = pd.DataFrame([[5, 'STATEN ISLAND', 'WOODROW', '123 FAKE STREET', None, None, False]],
                       columns=missing_rows.columns)
# Append the new row to the dataframe
missing_rows = missing_rows.append(new_row, ignore_index=True)

In [32]:
df_queryResponse

BOROUGH CODE        BOROUGH   NEIGHBORHOOD                   ADDRESS  \
0               5  STATEN ISLAND        WOODROW         40 HERRICK AVENUE   
1               5  STATEN ISLAND        WOODROW        104 GLADWIN STREET   
2               5  STATEN ISLAND        WOODROW         96 LENEVAR AVENUE   
3               5  STATEN ISLAND        WOODROW     401 BLOOMINGDALE ROAD   
4               5  STATEN ISLAND        WOODROW     3120 ARTHUR KILL ROAD   
..            ...            ...            ...                       ...   
100             1      MANHATTAN  ALPHABET CITY  383 EAST 10TH STREET, B1   
101             1      MANHATTAN  ALPHABET CITY  383 EAST 10TH STREET, D1   
102             1      MANHATTAN  ALPHABET CITY   182 EAST 2ND STREET, 1C   
103             1      MANHATTAN  ALPHABET CITY   503 EAST 13TH STRET, B4   
104             1      MANHATTAN  ALPHABET CITY   754 EAST 6TH STREET, 2B   

     LATITUDE  LONGITUDE  GEOCODING ERR  
0   40.530700 -74.219200              0  
1   40.531900 -74.222500              0  
2   40.538900 -74.209400              0  
3   40.534800 -74.218000              0  
4   40.543800 -74.233500              0  
..        ...        ...            ...  
100 40.726500 -73.977800              0  
101 40.726500 -73.977800              0  
102 40.722700 -73.984400              0  
103       nan        nan              1  
104 40.722500 -73.977300              0  

[105 rows x 7 columns]

In [33]:
missing_rows

BOROUGH CODE        BOROUGH   NEIGHBORHOOD                ADDRESS  \
0                 1      MANHATTAN  ALPHABET CITY    347 EAST 4TH STREET   
1                 1      MANHATTAN  ALPHABET CITY            19 AVENUE D   
2                 1      MANHATTAN  ALPHABET CITY           110 AVENUE C   
3                 1      MANHATTAN  ALPHABET CITY    326 EAST 4TH STREET   
4                 1      MANHATTAN  ALPHABET CITY    328 EAST 4TH STREET   
...             ...            ...            ...                    ...   
81399             5  STATEN ISLAND        WOODROW     104 GLADWIN STREET   
81400             5  STATEN ISLAND        WOODROW      96 LENEVAR AVENUE   
81401             5  STATEN ISLAND        WOODROW  401 BLOOMINGDALE ROAD   
81402             5  STATEN ISLAND        WOODROW  3120 ARTHUR KILL ROAD   
81403             5  STATEN ISLAND        WOODROW        123 FAKE STREET   

      LATITUDE LONGITUDE  GEOCODING ERR  
0         None      None          False  
1         None      None          False  
2         None      None          False  
3         None      None          False  
4         None      None          False  
...        ...       ...            ...  
81399     None      None          False  
81400     None      None          False  
81401     None      None          False  
81402     None      None          False  
81403     None      None          False  

[81404 rows x 7 columns]

In [36]:
# DANGEROUS! HIGH API USAGE!

# OLD
# Apply geolocator function to all rows in updated_df DataFrame
#missing_rows = missing_rows.apply(geolocate, axis=1)


# NEW
#for i in tqdm(missing_rows.index):
    #missing_rows.loc[i] = geolocate(missing_rows.loc[i])
    
# TEST NEW NEW
# # Select the first 10 rows of the DataFrame
# subset = missing_rows.tail(15)

# # Apply the function to the subset
# subset = subset.progress_apply(geolocate, axis=1)

# # Check the results
# print(subset)

# NEW NEW
tqdm.pandas()
missing_rows = missing_rows.progress_apply(geolocate, axis=1)
missing_rows.to_csv('geocodes_export.csv', index=False)

  0%|          | 0/81404 [00:00<?, ?it/s]

In [86]:
# engine = create_engine(f'mysql+pymysql://{username}:{password}@{hostname}/{database_name}')
upload_geocoding_dataframe_to_sql(engine, 'geocodes', missing_rows)

HELLOO WORLD
HELLOO WORLD2
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5
HELLOO WORLD4.6
HELLOO WORL5
HELLOO WORLD4
HELLOO WORLD4.5

KeyboardInterrupt: 

In [85]:
# Create the SQLAlchemy engine
engine = create_engine(f'mysql+pymysql://{username}:{password}@{hostname}/{database_name}')
# Call the function to print the SQL table
print_sql_table(engine, 'geocodes')

(5, 'STATEN ISLAND', 'WOODROW', '40 HERRICK AVENUE', 40.5307, -74.2192, 0, '5_STATEN ISLAND_40 HERRICK AVENUE')
(5, 'STATEN ISLAND', 'WOODROW', '104 GLADWIN STREET', 40.5319, -74.2225, 0, '5_STATEN ISLAND_104 GLADWIN STREET')
(5, 'STATEN ISLAND', 'WOODROW', '96 LENEVAR AVENUE', 40.5389, -74.2094, 0, '5_STATEN ISLAND_96 LENEVAR AVENUE')
(5, 'STATEN ISLAND', 'WOODROW', '401 BLOOMINGDALE ROAD', 40.5348, -74.218, 0, '5_STATEN ISLAND_401 BLOOMINGDALE ROAD')
(5, 'STATEN ISLAND', 'WOODROW', '3120 ARTHUR KILL ROAD', 40.5438, -74.2335, 0, '5_STATEN ISLAND_3120 ARTHUR KILL ROAD')
(5, 'STATEN ISLAND', 'WOODROW', '123 FAKE STREET', None, None, 1, '5_STATEN ISLAND_123 FAKE STREET')
(1, 'MANHATTAN', 'ALPHABET CITY', '347 EAST 4TH STREET', 40.7217, -73.9783, 0, '1_MANHATTAN_347 EAST 4TH STREET')
(1, 'MANHATTAN', 'ALPHABET CITY', '19 AVENUE D', 40.7207, -73.9785, 0, '1_MANHATTAN_19 AVENUE D')
(1, 'MANHATTAN', 'ALPHABET CITY', '110 AVENUE C', 40.7242, -73.9785, 0, '1_MANHATTAN_110 AVENUE C')
(1, 'MANHA

(1, 'MANHATTAN', 'CHELSEA', '127 7 AVENUE, 4D', 40.7408, -73.9977, 0, '1_MANHATTAN_127 7 AVENUE, 4D')
(1, 'MANHATTAN', 'CHELSEA', '127 7 AVENUE, 5A', 40.7408, -73.9977, 0, '1_MANHATTAN_127 7 AVENUE, 5A')
(1, 'MANHATTAN', 'CHELSEA', '127 SEVENTH AVENUE, 6C', 40.7408, -73.9977, 0, '1_MANHATTAN_127 SEVENTH AVENUE, 6C')
(1, 'MANHATTAN', 'CHELSEA', '127 7 AVENUE, 7C', 40.7408, -73.9977, 0, '1_MANHATTAN_127 7 AVENUE, 7C')
(1, 'MANHATTAN', 'CHELSEA', '130 W 19 ST, 12A', None, None, 1, '1_MANHATTAN_130 W 19 ST, 12A')
(1, 'MANHATTAN', 'CHELSEA', '130 WEST 19 STREET, 12C', 40.7409, -73.9962, 0, '1_MANHATTAN_130 WEST 19 STREET, 12C')
(1, 'MANHATTAN', 'CHELSEA', '163 WEST 18TH STREET, 1B', 40.7409, -73.9972, 0, '1_MANHATTAN_163 WEST 18TH STREET, 1B')
(1, 'MANHATTAN', 'CHELSEA', '163 WEST 18 STREET, 2B', None, None, 1, '1_MANHATTAN_163 WEST 18 STREET, 2B')
(1, 'MANHATTAN', 'CHELSEA', '155 WEST 18TH STREET, 201', 40.7409, -73.9969, 0, '1_MANHATTAN_155 WEST 18TH STREET, 201')
(1, 'MANHATTAN', 'CHELSE

(1, 'MANHATTAN', 'FASHION', '215 WEST 28TH STREET, 2A', 40.7477, -73.9941, 0, '1_MANHATTAN_215 WEST 28TH STREET, 2A')
(1, 'MANHATTAN', 'FASHION', '215 WEST 28TH STREET, 2B', 40.7477, -73.9941, 0, '1_MANHATTAN_215 WEST 28TH STREET, 2B')
(1, 'MANHATTAN', 'FASHION', '215 WEST 28TH STREET, 2D', 40.7477, -73.9941, 0, '1_MANHATTAN_215 WEST 28TH STREET, 2D')
(1, 'MANHATTAN', 'FASHION', '215 WEST 28TH STREET, 2E', 40.7477, -73.9941, 0, '1_MANHATTAN_215 WEST 28TH STREET, 2E')
(1, 'MANHATTAN', 'FASHION', '215 WEST 28TH STREET, 2F', 40.7477, -73.9941, 0, '1_MANHATTAN_215 WEST 28TH STREET, 2F')
(1, 'MANHATTAN', 'FASHION', '215 WEST 28TH STREET, 2G', 40.7477, -73.9941, 0, '1_MANHATTAN_215 WEST 28TH STREET, 2G')
(1, 'MANHATTAN', 'FASHION', '215 WEST 28TH STREET, 3A', 40.7477, -73.9941, 0, '1_MANHATTAN_215 WEST 28TH STREET, 3A')
(1, 'MANHATTAN', 'FASHION', '215 WEST 28TH STREET, 3B', 40.7477, -73.9941, 0, '1_MANHATTAN_215 WEST 28TH STREET, 3B')
(1, 'MANHATTAN', 'FASHION', '215 WEST 28TH STREET, 3C', 

(1, 'MANHATTAN', 'FLATIRON', '5 EAST 22ND STREET, 11T', 40.7408, -73.9889, 0, '1_MANHATTAN_5 EAST 22ND STREET, 11T')
(1, 'MANHATTAN', 'FLATIRON', '23 EAST 22ND STREET, 11A', 40.7403, -73.9882, 0, '1_MANHATTAN_23 EAST 22ND STREET, 11A')
(1, 'MANHATTAN', 'FLATIRON', '23 EAST 22ND STREET, 20A', 40.7403, -73.9882, 0, '1_MANHATTAN_23 EAST 22ND STREET, 20A')
(1, 'MANHATTAN', 'FLATIRON', '23 EAST 22ND STREET, 41A', 40.7403, -73.9882, 0, '1_MANHATTAN_23 EAST 22ND STREET, 41A')
(1, 'MANHATTAN', 'FLATIRON', '23 EAST 22ND STREET, 57A', 40.7403, -73.9882, 0, '1_MANHATTAN_23 EAST 22ND STREET, 57A')
(1, 'MANHATTAN', 'FLATIRON', '45 EAST 22ND STREET, 14A', 40.74, -73.9873, 0, '1_MANHATTAN_45 EAST 22ND STREET, 14A')
(1, 'MANHATTAN', 'FLATIRON', '45 EAST 22ND STREET, 33B', 40.74, -73.9873, 0, '1_MANHATTAN_45 EAST 22ND STREET, 33B')
(1, 'MANHATTAN', 'FLATIRON', '45 EAST 22ND STREET, 46A', 40.74, -73.9873, 0, '1_MANHATTAN_45 EAST 22ND STREET, 46A')
(1, 'MANHATTAN', 'FLATIRON', '45 EAST 22ND STREET, 60A',

(1, 'MANHATTAN', 'GREENWICH VILLAGE-CENTRAL', '45 WEST 10TH STREET, 7CD', None, None, 1, '1_MANHATTAN_45 WEST 10TH STREET, 7CD')
(1, 'MANHATTAN', 'GREENWICH VILLAGE-CENTRAL', '45 WEST 10TH STREET, HLWY', None, None, 1, '1_MANHATTAN_45 WEST 10TH STREET, HLWY')
(1, 'MANHATTAN', 'GREENWICH VILLAGE-CENTRAL', '45 WEST 10TH STREET, PHAB', None, None, 1, '1_MANHATTAN_45 WEST 10TH STREET, PHAB')
(1, 'MANHATTAN', 'GREENWICH VILLAGE-CENTRAL', '45 WEST 11TH STREET, 2B', 40.7349, -73.9967, 0, '1_MANHATTAN_45 WEST 11TH STREET, 2B')
(1, 'MANHATTAN', 'GREENWICH VILLAGE-CENTRAL', '45 WEST 11TH STREET, GD', None, None, 1, '1_MANHATTAN_45 WEST 11TH STREET, GD')
(1, 'MANHATTAN', 'GREENWICH VILLAGE-CENTRAL', '79 WEST 12 STREET, 14B', 40.736, -73.9974, 0, '1_MANHATTAN_79 WEST 12 STREET, 14B')
(1, 'MANHATTAN', 'GREENWICH VILLAGE-CENTRAL', '79 WEST 12 STREET, 8A', 40.736, -73.9974, 0, '1_MANHATTAN_79 WEST 12 STREET, 8A')
(1, 'MANHATTAN', 'GREENWICH VILLAGE-CENTRAL', '79 WEST 12TH STREET, 10F', 40.736, -73.99

...

(3, 'BROOKLYN', 'DYKER HEIGHTS', '1160 66TH STREET', 40.627, -74.0052, 0, '3_BROOKLYN_1160 66TH STREET')
(3, 'BROOKLYN', 'DYKER HEIGHTS', '1283 67TH STREET', 40.6251, -74.0029, 0, '3_BROOKLYN_1283 67TH STREET')
(3, 'BROOKLYN', 'DYKER HEIGHTS', '957 68TH STREET', 40.6289, -74.0105, 0, '3_BROOKLYN_957 68TH STREET')
(3, 'BROOKLYN', 'DYKER HEIGHTS', '1216 67TH STREET', 40.6257, -74.0046, 0, '3_BROOKLYN_1216 67TH STREET')
(3, 'BROOKLYN', 'DYKER HEIGHTS', '1372 67TH STREET', 40.6236, -74.0011, 0, '3_BROOKLYN_1372 67TH STREET')
(3, 'BROOKLYN', 'DYKER HEIGHTS', '1052 68TH STREET', 40.6272, -74.0089, 0, '3_BROOKLYN_1052 68TH STREET')
(3, 'BROOKLYN', 'DYKER HEIGHTS', '1357 BAY RIDGE AVENUE', 40.623, -74.0023, 0, '3_BROOKLYN_1357 BAY RIDGE AVENUE')
(3, 'BROOKLYN', 'DYKER HEIGHTS', '948 BAY RIDGE AVE', 40.6282, -74.0117, 0, '3_BROOKLYN_948 BAY RIDGE AVE')
(3, 'BROOKLYN', 'DYKER HEIGHTS', '963 71ST STREET', 40.6271, -74.0121, 0, '3_BROOKLYN_963 71ST STREET')
(3, 'BROOKLYN', 'DYKER HEIGHTS', '1078 7

(3, 'BROOKLYN', 'FLATBUSH-CENTRAL', '2913 NEWKIRK AVENUE', 40.6402, -73.9489, 0, '3_BROOKLYN_2913 NEWKIRK AVENUE')
(3, 'BROOKLYN', 'FLATBUSH-CENTRAL', '512 EAST 23RD STREET', 40.6373, -73.9559, 0, '3_BROOKLYN_512 EAST 23RD STREET')
(3, 'BROOKLYN', 'FLATBUSH-CENTRAL', '474 EAST 24TH STREET', 40.6376, -73.955, 0, '3_BROOKLYN_474 EAST 24TH STREET')
(3, 'BROOKLYN', 'FLATBUSH-CENTRAL', '2345 FOSTER AVENUE', 40.6385, -73.9546, 0, '3_BROOKLYN_2345 FOSTER AVENUE')
(3, 'BROOKLYN', 'FLATBUSH-CENTRAL', '531 EAST 26TH STREET', 40.6376, -73.9518, 0, '3_BROOKLYN_531 EAST 26TH STREET')
(3, 'BROOKLYN', 'FLATBUSH-CENTRAL', '1302 ROGERS AVENUE', 40.638, -73.9514, 0, '3_BROOKLYN_1302 ROGERS AVENUE')
(3, 'BROOKLYN', 'FLATBUSH-CENTRAL', '549 EAST 26TH STREET', 40.6372, -73.9518, 0, '3_BROOKLYN_549 EAST 26TH STREET')
(3, 'BROOKLYN', 'FLATBUSH-CENTRAL', '2805 FARRAGUT ROAD', 40.6364, -73.9497, 0, '3_BROOKLYN_2805 FARRAGUT ROAD')
(3, 'BROOKLYN', 'FLATBUSH-CENTRAL', '526 EAST 29TH STREET', 40.6378, -73.9494, 0

(3, 'BROOKLYN', 'FLATBUSH-EAST', '282 EAST 35TH STREET, 3W', 40.6484, -73.9446, 0, '3_BROOKLYN_282 EAST 35TH STREET, 3W')
(3, 'BROOKLYN', 'FLATBUSH-EAST', '282 EAST 35TH STREET, 4M', 40.6484, -73.9446, 0, '3_BROOKLYN_282 EAST 35TH STREET, 4M')
(3, 'BROOKLYN', 'FLATBUSH-EAST', '282 EAST 35TH STREET, 7R', 40.6484, -73.9446, 0, '3_BROOKLYN_282 EAST 35TH STREET, 7R')
(3, 'BROOKLYN', 'FLATBUSH-EAST', '282 EAST 35TH STREET, 7V', 40.6484, -73.9446, 0, '3_BROOKLYN_282 EAST 35TH STREET, 7V')
(3, 'BROOKLYN', 'FLATBUSH-EAST', '3500 SNYDER AVE, 4Y', 40.6491, -73.9441, 0, '3_BROOKLYN_3500 SNYDER AVE, 4Y')
(3, 'BROOKLYN', 'FLATBUSH-EAST', '3500 SNYDER AVE, 7B', 40.6491, -73.9441, 0, '3_BROOKLYN_3500 SNYDER AVE, 7B')
(3, 'BROOKLYN', 'FLATBUSH-EAST', '3500 SNYDER AVE, 7R', 40.6491, -73.9441, 0, '3_BROOKLYN_3500 SNYDER AVE, 7R')
(3, 'BROOKLYN', 'FLATBUSH-EAST', '3500 SNYDER AVE, 7Y', 40.6491, -73.9441, 0, '3_BROOKLYN_3500 SNYDER AVE, 7Y')
(3, 'BROOKLYN', 'FLATBUSH-EAST', '3500 SNYDER AVENUE, 6W', 40.64

(3, 'BROOKLYN', 'GERRITSEN BEACH', '47 EBONY COURT', 40.5928, -73.9284, 0, '3_BROOKLYN_47 EBONY COURT')
(3, 'BROOKLYN', 'GERRITSEN BEACH', '76 DICTUM COURT', 40.5943, -73.9293, 0, '3_BROOKLYN_76 DICTUM COURT')
(3, 'BROOKLYN', 'GERRITSEN BEACH', '26 LOIS AVENUE', 40.5873, -73.9205, 0, '3_BROOKLYN_26 LOIS AVENUE')
(3, 'BROOKLYN', 'GERRITSEN BEACH', '95 BARTLETT PLACE', 40.5907, -73.9244, 0, '3_BROOKLYN_95 BARTLETT PLACE')
(3, 'BROOKLYN', 'GERRITSEN BEACH', '91 ASTER COURT', 40.5954, -73.929, 0, '3_BROOKLYN_91 ASTER COURT')
(3, 'BROOKLYN', 'GERRITSEN BEACH', '99 EBONY COURT', 40.5948, -73.9309, 0, '3_BROOKLYN_99 EBONY COURT')
(3, 'BROOKLYN', 'GERRITSEN BEACH', '2934 GERRITSEN AVENUE', 40.5891, -73.9213, 0, '3_BROOKLYN_2934 GERRITSEN AVENUE')
(3, 'BROOKLYN', 'GERRITSEN BEACH', '2716 GERRITSEN AVENUE', 40.5928, -73.9255, 0, '3_BROOKLYN_2716 GERRITSEN AVENUE')
(3, 'BROOKLYN', 'GERRITSEN BEACH', '96 EBONY COURT', 40.5947, -73.9304, 0, '3_BROOKLYN_96 EBONY COURT')
(3, 'BROOKLYN', 'GERRITSEN BE

KeyboardInterrupt: 

In [35]:
missing_rows.to_csv('geocodes_export_next.csv', index=False)

In [66]:
with engine.connect() as connection:
    connection.execute(text("ALTER TABLE geocodes ADD PRIMARY_KEY VARCHAR(255)"))
    connection.execute(text("UPDATE geocodes SET PRIMARY_KEY = CONCAT(`BOROUGH CODE`, '_', `BOROUGH`, '_', `ADDRESS`)"))


In [60]:
text(f'UPDATE {geocodes_sql_table} SET PRIMARY_KEY = CONCAT([BOROUGH CODE], '_', [BOROUGH], '_', [ADDRESS])')






SyntaxError: invalid syntax (<ipython-input-60-90c269e5d287>, line 1)

In [ ]:
with engine.connect() as connection:
    result = connection.execute(text("SELECT * FROM geocodes LIMIT 2;"))
    tables = [(row[0],row[1],row[2],row[3],row[4],row[5],row[6],row[7]) for row in result]
    print(tables)